In [1]:
import random
import time
import pandas as pd
from bs4 import BeautifulSoup as bs
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import undetected_chromedriver as uc

# Configura el navegador con undetected_chromedriver y un User-Agent aleatorio
options = uc.ChromeOptions()
user_agents = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/93.0.4577.63 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:90.0) Gecko/20100101 Firefox/90.0",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Edge/91.0.864.67 Safari/537.36"
]
options.add_argument(f"user-agent={random.choice(user_agents)}")
browser = uc.Chrome(options=options)

# URL inicial: Página de listados de Madrid
url = "https://www.pisos.com/venta/pisos-madrid/"
browser.get(url)

# Manejar las cookies
try:
    WebDriverWait(browser, 20).until(
        EC.element_to_be_clickable((By.XPATH, '//*[@id="didomi-notice-agree-button"]'))
    ).click()
except:
    pass  # No mostramos mensaje si el botón de cookies no está presente

# Espera a que los inmuebles se carguen en la página principal
try:
    WebDriverWait(browser, 20).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, '.ad-preview'))
    )
except:
    browser.quit()

# Hacer clic en la primera caja de la lista de inmuebles
try:
    primer_inmueble = WebDriverWait(browser, 10).until(
        EC.element_to_be_clickable((By.CSS_SELECTOR, '.ad-preview'))
    )
    primer_inmueble.click()
    time.sleep(random.uniform(10, 12))  # Espera para evitar detección
except:
    browser.quit()

# Lista para almacenar los datos
all_data = []
registro_count = 0  # Contador de registros
max_registros = 11000  # Límite de registros a procesar

# Bucle para iterar desde el primer inmueble a los siguientes inmuebles desde su página
while registro_count < max_registros:
    try:
        # Extraer la información del inmueble actual
        html_inmueble = browser.page_source
        soup_inmueble = bs(html_inmueble, 'lxml')
        url_actual = browser.current_url

        # Intentar extraer datos del inmueble
        try:
            # Precio
            precio = soup_inmueble.find('div', {'class': 'price__value jsPriceValue'}).text.split(' ')[0] if soup_inmueble.find('div', {'class': 'price__value jsPriceValue'}) else "N/A"

            # Superficie construida
            superficie_construida = soup_inmueble.find('span', {'class': 'features__value'}).text.split(' ')[0] if soup_inmueble.find('span', {'class': 'features__value'}) else "N/A"

            # Última actualización
            ultima_actualizacion = soup_inmueble.find('p', {'class': 'last-update__date'}).text if soup_inmueble.find('p', {'class': 'last-update__date'}) else "N/A"

            # Características
            c1 = soup_inmueble.find('div', {'class': 'features__content'})
            features_list = []
            if c1:
                features = c1.find_all('div', {'class': 'features__feature'})
                for feature in features:
                    label = feature.find('span', {'class': 'features__label'}).get_text(strip=True)
                    value = feature.find('span', {'class': 'features__value'}).get_text(strip=True)
                    features_list.append((label, value))

            # Certificado energético
            try:
                energy_certificate = soup_inmueble.find('div', {'class': 'details__block energy-certificate'})
                consumo = energy_certificate.find('div', {'class': 'energy-certificate__data'}).find_all('span')[1].get_text(strip=True)
                emisiones = energy_certificate.find_all('div', {'class': 'energy-certificate__data'})[1].find_all('span')[1].get_text(strip=True)
            except AttributeError:
                consumo = "N/A"
                emisiones = "N/A"

        except:
            # Si falla la extracción de datos, asigna valores "N/A" pero sigue contabilizando el registro
            precio = "N/A"
            superficie_construida = "N/A"
            ultima_actualizacion = "N/A"
            features_list = []
            consumo = "N/A"
            emisiones = "N/A"

        # Guarda los datos en una lista
        data = {
            'Enlace': url_actual,
            'Precio': precio,
            'Superficie Construida': superficie_construida,
            'Última Actualización': ultima_actualizacion,
            'Consumo Energético': consumo,
            'Emisiones CO2': emisiones,
            'Características': features_list,
            'Tipo de operación': 'Compra'
        }

        all_data.append(data)
        registro_count += 1  # Incrementar el contador de registros

        # Imprime los datos de la página actual, incluso si hay errores
        print(f"Inmueble {registro_count}: {data}")

        # Pausar cada 400 registros
        if registro_count % 400 == 0:
            pausa = random.uniform(45, 60)
            print(f"Pausa de {pausa:.2f} segundos tras {registro_count} registros.")
            time.sleep(pausa)

        # Intenta hacer clic en el botón de "Siguiente" para ir al siguiente inmueble
        try:
            siguiente_boton = WebDriverWait(browser, 10).until(
                EC.element_to_be_clickable((By.CSS_SELECTOR, ".navigation-arrow--next"))
            )
            siguiente_boton.click()

            # Pausa aleatoria para simular el comportamiento humano y evitar bloqueo
            # time.sleep(random.uniform(1, 3))

        except:
            print("No se encontró el botón 'Siguiente' o ya no hay más inmuebles.")
            break

    except:
        break  # Ignorar errores al cargar la página del inmueble y continuar con el siguiente

# Una vez terminado el bucle, puedes convertir los datos en un DataFrame de pandas y guardarlos
df = pd.DataFrame(all_data)
print(df)

# Opcional: guarda el DataFrame en un archivo CSV
df.to_csv('data_02pisoscompra.csv', index=False)

# Cierra el navegador
browser.quit()

Inmueble 1: {'Enlace': 'https://www.pisos.com/comprar/chalet-villalbilla_centro_urbano-3032755362_109700/', 'Precio': '310.000', 'Superficie Construida': '181', 'Última Actualización': 'Anuncio actualizado el 09/08/2024', 'Consumo Energético': 'Consumo:27 kWh/m² año', 'Emisiones CO2': 'Emisiones:6 Kg CO₂/m² año', 'Características': [('Superficie construida:', '181 m²'), ('Habitaciones:', '4'), ('Baños:', '3'), ('Conservación:', 'A estrenar'), ('Referencia:', '4995907-19514080')], 'Tipo de operación': 'Compra'}
Inmueble 2: {'Enlace': 'https://www.pisos.com/comprar/casa_unifamiliar-villalbilla_centro_urbano-20842409004_995907/', 'Precio': '310.000', 'Superficie Construida': '180', 'Última Actualización': 'Anuncio actualizado el 28/10/2024', 'Consumo Energético': 'Consumo:27 kWh/m² año', 'Emisiones CO2': 'Emisiones:6 Kg CO₂/m² año', 'Características': [('Superficie construida:', '180 m²'), ('Superficie útil:', '152 m²'), ('Superficie solar:', '150 m²'), ('Habitaciones:', '4'), ('Baños:', 